In [21]:
from pathlib import Path
import numpy as np
import plotly

CURRENT_DIR = Path('.')
DATA_DIR = CURRENT_DIR / '../data'

In [22]:
all_npy_files = [x for x in DATA_DIR.rglob('*.npy')]

In [23]:
file = [x for x in all_npy_files if 'a104i104-1500-1630.npy' in x.name][0]

In [24]:
a = np.load(file)

In [25]:
# normalized_array = (a - a.min()) / (a.max() - a.min())
normalized_array = a  / a.max()

In [26]:
orig_power_values = normalized_array.tolist()[0]

In [27]:
def get_wavelength_range(start, end):
    wavelenght_values = np.arange(start_point, end_point, (end_point - start_point) / len(orig_power_values)).tolist()

    return wavelenght_values

In [28]:
import plotly.express as px
import plotly.graph_objects as go

def get_fig(power_values, wavelenght_values):

    fig = go.Figure([go.Scatter(x=wavelenght_values, y=power_values)])

    return fig


In [29]:
start_point, end_point = 1500, 1630
orig_wavelength_values = get_wavelength_range(start_point, end_point)

# Plot original figure

In [30]:
orig_fig = get_fig(orig_power_values, orig_wavelength_values)

orig_fig.show()

In [31]:
## Plot chunk of data

In [32]:
# plot chunk of data
chunk_start, chunk_end = 1622, 1628
chunk_start_index = np.abs(np.array(orig_wavelength_values)-chunk_start).argmin() 
chunk_end_index = np.abs(np.array(orig_wavelength_values)-chunk_end).argmin()

chunk_power_values = orig_power_values[chunk_start_index:chunk_end_index]
chunk_wavelength_values = orig_wavelength_values[chunk_start_index:chunk_end_index]

In [33]:
chunk_fig = get_fig(chunk_power_values, chunk_wavelength_values)

chunk_fig.show()

## Downsample 

In [39]:
def get_fig_with_downsampled_curve(power_values, ds_power_values, wavelength_values, ds_wavelength_values):
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        name="Original curve",
        mode="lines", x=wavelength_values, y=power_values))

    fig.add_trace(go.Scatter(
        name="Downsampled curve",
        mode="lines", x=ds_wavelength_values, y=ds_power_values))

    return fig

In [42]:
donwsampled_rate = 100

ds_chunk_power_values = chunk_power_values[::donwsampled_rate]
ds_chunk_wavelength_values = chunk_wavelength_values[::donwsampled_rate]


In [43]:
ds_chunk_fig = get_fig_with_downsampled_curve(chunk_power_values, ds_chunk_power_values, chunk_wavelength_values, ds_chunk_wavelength_values)

ds_chunk_fig.show()

## Fit a Lorentzian curve

In [47]:
import numpy as np
from scipy.optimize import leastsq

def lorentzian(x, x0, a, gam):
    return a * gam**2 / ( gam**2 + ( x - x0 )**2)

def multi_lorentz( x, params ):
    off = params[0]
    paramsRest = params[1:]
    assert not ( len( paramsRest ) % 3 )
    return off + sum( [ lorentzian( x, *paramsRest[ i : i+3 ] ) for i in range( 0, len( paramsRest ), 3 ) ] )

def res_multi_lorentz( params, xData, yData ):
    diff = [ multi_lorentz( x, params ) - y for x, y in zip( xData, yData ) ]
    return diff


def fit_lorentzian(power_values, wavelenght_values):
    yData = np.array(power_values)
    xData = np.array(wavelenght_values)
    # yData = yData / max(yData)

    generalWidth = 1

    yDataLoc = yData
    startValues = [ max( yData ) ]
    counter = 0

    while max( yDataLoc ) - min( yDataLoc ) > .1:
        print(counter)
        counter += 1
        if counter > 20: ### max 20 peak...emergency break to avoid infinite loop
            break
        minP = np.argmin( yDataLoc )
        minY = yData[ minP ]
        x0 = xData[ minP ]
        startValues += [ x0, minY - max( yDataLoc ), generalWidth ]
        popt, ier = leastsq( res_multi_lorentz, startValues, args=( xData, yData ) )
        yDataLoc = [ y - multi_lorentz( x, popt ) for x,y in zip( xData, yData ) ]

    fitted_lorentzian_values = [ multi_lorentz(x, popt ) for x in xData ]

    return fitted_lorentzian_values, popt

In [48]:
def calculate_qf(fitted_lorentzian_values, wavelenght_values, params):
    x0 = wavelenght_values[np.argmin(fitted_lorentzian_values)]
    gamma = np.abs(params[-1])

    return x0 / gamma

In [49]:
def get_fig_with_lorentzian_trace(power_values, fitted_power_values, wavelength_values):
    fig = go.Figure()
    fig.add_trace(go.Scatter(
        name="Measured values",
        mode="lines", x=wavelength_values, y=power_values))

    fig.add_trace(go.Scatter(
        name="Fitted Lorentzian",
        mode="lines", x=wavelength_values, y=fitted_power_values))

    return fig

## Fit curve for the selected chunk

In [50]:
fitted_curve, params = fit_lorentzian(chunk_power_values, chunk_wavelength_values)

0


In [51]:
lorentzoian_fig = get_fig_with_lorentzian_trace(chunk_power_values, fitted_curve, chunk_wavelength_values)
lorentzoian_fig.show()

In [44]:
# plotly.offline.plot(lorentzoian_fig, filename='chunk_lorentz.html') 

In [52]:
qf = calculate_qf(fitted_curve,chunk_wavelength_values,params)
qf

11196.542609631946

## Fit curve for the whole measurements

In [55]:
fitted_curve_whole, params_whole = fit_lorentzian(orig_power_values, orig_wavelength_values)

0
1


KeyboardInterrupt: 